# 事前準備

In [ ]:
%%javascript
function ClickConnect(){
console.log("Working");
document.querySelector("colab-toolbar-button#connect").click()
}setInterval(ClickConnect,60000)

<IPython.core.display.Javascript object>

In [ ]:
#デフォルトGドライブパス
fldGdrive = '/content/drive/'
fldGdriveColabMyDrive = fldGdrive + 'MyDrive/'
fldGdriveColabMyDriveData = fldGdriveColabMyDrive + 'Colab Notebooks/data/'

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install -qU torch==1.7.1 torchtext==0.8.0 torchvision==0.8.2 torchaudio==0.7.2
!pip install -q transformers==4.4.2 sentencepiece

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 776.8/776.8 MB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 96.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 99.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 99.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 44.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 65.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 880.6/880.6 KB 60.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 10.0 MB/s eta 0:00:00


In [ ]:
# 転移学習済みモデル
MODEL_DIR = "sonoisa/t5-base-japanese-title-generation"

In [ ]:
#文字列の正規化の定義
#表記揺れを減らします。今回はneologdの正規化処理を一部改変したものを利用します。 処理の詳細はリンク先を参照してください。
# https://github.com/neologd/mecab-ipadic-neologd/wiki/Regexp.ja から引用・一部改変
from __future__ import unicode_literals
import re
import unicodedata

def unicode_normalize(cls, s):
    pt = re.compile('([{}]+)'.format(cls))

    def norm(c):
        return unicodedata.normalize('NFKC', c) if pt.match(c) else c

    s = ''.join(norm(x) for x in re.split(pt, s))
    s = re.sub('－', '-', s)
    return s

def remove_extra_spaces(s):
    s = re.sub('[ 　]+', ' ', s)
    blocks = ''.join(('\u4E00-\u9FFF',  # CJK UNIFIED IDEOGRAPHS
                      '\u3040-\u309F',  # HIRAGANA
                      '\u30A0-\u30FF',  # KATAKANA
                      '\u3000-\u303F',  # CJK SYMBOLS AND PUNCTUATION
                      '\uFF00-\uFFEF'   # HALFWIDTH AND FULLWIDTH FORMS
                      ))
    basic_latin = '\u0000-\u007F'

    def remove_space_between(cls1, cls2, s):
        p = re.compile('([{}]) ([{}])'.format(cls1, cls2))
        while p.search(s):
            s = p.sub(r'\1\2', s)
        return s

    s = remove_space_between(blocks, blocks, s)
    s = remove_space_between(blocks, basic_latin, s)
    s = remove_space_between(basic_latin, blocks, s)
    return s

def normalize_neologd(s):
    s = s.strip()
    s = unicode_normalize('０-９Ａ-Ｚａ-ｚ｡-ﾟ', s)

    def maketrans(f, t):
        return {ord(x): ord(y) for x, y in zip(f, t)}

    s = re.sub('[˗֊‐‑‒–⁃⁻₋−]+', '-', s)  # normalize hyphens
    s = re.sub('[﹣－ｰ—―─━ー]+', 'ー', s)  # normalize choonpus
    s = re.sub('[~∼∾〜〰～]+', '〜', s)  # normalize tildes (modified by Isao Sonobe)
    s = s.translate(
        maketrans('!"#$%&\'()*+,-./:;<=>?@[¥]^_`{|}~｡､･｢｣',
              '！”＃＄％＆’（）＊＋，－．／：；＜＝＞？＠［￥］＾＿｀｛｜｝〜。、・「」'))

    s = remove_extra_spaces(s)
    s = unicode_normalize('！”＃＄％＆’（）＊＋，－．／：；＜＞？＠［￥］＾＿｀｛｜｝〜', s)  # keep ＝,・,「,」
    s = re.sub('[’]', '\'', s)
    s = re.sub('[”]', '"', s)
    return s

In [ ]:
%cd /content/drive/MyDrive/Colab Notebooks/data/
%ls

/content/drive/MyDrive/Colab Notebooks/data
aoscs_20230113_prodcuts_descriptions_1_1000.tar.gz  livedoorNemsSample/
input/                                              output/
ldcc-20140209.tar.gz


In [ ]:
#情報抽出

import tarfile
import re
target_genres = ["products"]

tar_file_name = "aoscs_20230113_prodcuts_descriptions_1_1000.tar.gz"

def remove_brackets(text):
    text = re.sub(r"(^【[^】]*】)|(【[^】]*】$)", "", text)
    return text

def normalize_text(text):
    assert "\n" not in text and "\r" not in text
    text = text.replace("\t", " ")
    text = text.strip()
    text = normalize_neologd(text)
    text = text.lower()
    return text

genre_files_list = [[] for genre in target_genres]

all_data = []

def read_id_name_desc(file):
    line = next(file).decode("utf-8").strip()
    line = normalize_text(remove_brackets(line))
    row = line.split('|')
    id = row[0].split(",")[1]
    name = row[1]
    desc = row[2]
    return id, name, desc
                
def read_tarfile():
  with tarfile.open(tar_file_name) as archive_file:
      for archive_item in archive_file:
          for i, genre in enumerate(target_genres):
              if genre in archive_item.name and archive_item.name.endswith(".txt"):
                  #print(archive_item.name)
                  #print(archive_item.name.endswith(".txt"))
                  genre_files_list[i].append(archive_item.name)
      for i, genre_files in enumerate(genre_files_list):
          for name in genre_files:
              file = archive_file.extractfile(name)
              id, name, desc = read_id_name_desc(file)
              print(id, name)

              if len(id) > 0 and len(name) > 0:
                  all_data.append({
                      "id": id,
                      "name": name,
                      "descrption": desc
                      })

read_tarfile()

print(all_data)

69855 ビジネスバッグ【ace】【エキスパンダブル】
71209 プレミアムレギュラータイ【made in italy】
71187 プレミアムレギュラータイ【made in italy】
69691 ボタンダウンスタイリッシュワイシャツ【tiotio premium】
69456 ボタンダウンスタンダードワイシャツ【キング&トール】【non ironmax】
72336 ワイドカラースタイリッシュワイシャツ
72192 ワイドカラースタイリッシュワイシャツ【non irontech】【tiotiopremium】
68450 ワイドカラースタンダードワイシャツ【キング&トール】【non irontech】
71198 プレミアムレギュラータイ【made in italy】
68456 ワイドカラースタンダードワイシャツ【non irontech】
70593 ナロータイ【ストライプ】
70369 レギュラータイ
70381 レギュラータイ
70343 プレミアムレギュラータイ【西陣織】
70564 ノータックテーパードパンツ【セットアップ】
70969 プレミアムスタイリッシュスーツ【御幸毛織】【made in japan pride】
70014 ボタンダウンスタンダードワイシャツ【キング&トール】【lenzing ecovero】
69998 レギュラーカラースタイリッシュワイシャツ
71211 プレミアムレギュラータイ【made in italy】
71239 レギュラータイ【oeko-tex】
69790 ボタンダウンスタイリッシュワイシャツ【lenzing ecovero】
68433 ボタンダウンスタイリッシュワイシャツ【non irontech】
68430 スタイリッシュスーツ【activexpand】
68721 ワイドカラースタイリッシュワイシャツ【non irontech】
67861 プレミアムレギュラータイ【hilton】
67929 ボタンダウンスタンダードワイシャツ【tiotio premium】
67879 プレミアムレギュラータイ【fresco tie】
67873 プレミアムレギュラータイ【fresco tie】
67485 プレミアムスタイリッシュスーツ【ツーパンツ】【super110's】
67878 プレミアムレギュラ

In [ ]:
'''
データ分割
データセットを90% : 5%: 5% の比率でtrain/dev/testに分割します。

trainデータ: 学習に利用するデータ
devデータ: 学習中の精度評価等に利用するデータ
testデータ: 学習結果のモデルの精度評価に利用するデータ
'''
import random
from tqdm import tqdm

random.seed(1234)
random.shuffle(all_data)

def to_line(data):
    id = data["id"]
    name = data["name"]
    descrption = data["descrption"]
    assert len(id) > 0 and len(name) > 0
    return f"{id}\t{name}\t{descrption}\n"

data_size = len(all_data)
train_ratio, dev_ratio, test_ratio = 0.9, 0.05, 0.05

with open(f"/content/train2.tsv", "w", encoding="utf-8") as f_train, \
    open(f"/content/dev2.tsv", "w", encoding="utf-8") as f_dev, \
    open(f"/content/test2.tsv", "w", encoding="utf-8") as f_test:
    for i, data in tqdm(enumerate(all_data)):
        line = to_line(data)
        if i < train_ratio * data_size:
            f_train.write(line)
        elif i < (train_ratio + dev_ratio) * data_size:
            f_dev.write(line)
        else:
            f_test.write(line)

1000it [00:00, 91761.01it/s]


In [ ]:
#作成されたデータを確認します。
#形式: {タイトル}\t{本文}\t{ジャンルID}
!head -3 /content/test2.tsv

34395	スクールシャツ【長袖】【レギュラーカラー】	【形態安定性に優れた長袖スクールシャツ】ポリエステルと綿を混紡した生地を使用したスクールシャツです。形態安定性に優れた生地は家庭洗濯可能でシワになりにくく、お手入れも簡単です。吸水防汚加工を加え衿や袖口などは汚れにくく、汗などの水分は吸い取りやすく仕上がりました。衿型はスタンダードなレギュラーカラー、左胸にポケットが1つ付いています。お手入れ簡単なスクールシャツは新入学の方から買い替えの方まで、満足していただける、おすすめの1枚です。■ゆとり感には個人差があります【商品サイズ表】確認の上ご購入の目安としてご利用ください。■サイズ選択は身長サイズからの選択となり、袖丈などは商品サイズ表からご確認ください。■モニター・パソコン環境により色味に誤差が生じる場合がございます。予めご了承くださいませ。学生服について詳しくはこちら
71096	レギュラータイ【oeko-tex】	【商品詳細】織柄で様々な質感を表現することで、無地でありながらも、表情豊かなソリッドタイシリーズです。シルク100%の素材の生地感が光沢感と柔らかみのある雰囲気で、ビジネススタイルに飽きのこないお洒落を演出してくれます。合わせるアイテムを選ばないシンプルなデザインのため、コーディネートの幅を広げてくれる、汎用性の高いネクタイです。また、タイバーを合わせることによりネクタイの曲りを抑え、綺麗な身だしなみに仕上がりビジネスマンの大事な胸元を綺麗に整えます。■oeko-tex(エコテックス)繊維製品の国際的な安全基準であるエコテックスに認証された素材を使用しました。生地から付属まで、すべてが厳しい基準をクリアした素材を使用、安全を安心して着用いただけます。【商品に関するご注意】■ブラウザやお使いのモニター環境、室内外等の撮影時の環境下での光加減により、実際の商品と掲載画像の色味が異なる場合がございます。■平置き・メジャーでの採寸の為、素材や仕様等により実際の商品とサイズに若干の誤差が生じる場合がございます。予めご了承ください。
71063	レギュラータイ【return to natural】	【商品詳細】『person's for men』スーツからジャケットまでスタイリッシュに胸元を飾るネクタイです。ベーシックな色柄でコーディネートもしやすく、初めてネ

# 推論に必要なクラス等の定義
推論にはPyTorch/Transformersを利用します。

In [ ]:
import argparse
import glob
import os
import json
import time
import logging
import random
import re
from itertools import chain
from string import punctuation

import numpy as np
import torch
from torch.utils.data import Dataset, DataLoader


from transformers import (
    T5ForConditionalGeneration,
    T5Tokenizer,
)

# 乱数シードの設定
def set_seed(seed):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    if torch.cuda.is_available():
        torch.cuda.manual_seed_all(seed)

set_seed(42)

In [ ]:
# GPU利用有無
USE_GPU = torch.cuda.is_available()
print(USE_GPU)

# 各種ハイパーパラメータ
args_dict = dict(
    data_dir="/content",  # データセットのディレクトリ
    model_name_or_path=MODEL_DIR,
    tokenizer_name_or_path=MODEL_DIR,

    max_input_length=512,
    max_target_length=64,

    n_gpu=1 if USE_GPU else 0,
    early_stop_callback=False,
    fp_16=False,
    opt_level='O1',
    max_grad_norm=1.0,
    seed=42,
)

True


# TSVデータセットクラス
TSV形式のファイルをデータセットとして読み込みます。
形式は"{title}\t{body}\t{genre_id}"です。

In [ ]:
class TsvDataset(Dataset):
    def __init__(self, tokenizer, data_dir, type_path, input_max_len=512, target_max_len=512):
        self.file_path = os.path.join(data_dir, type_path)

        print(self.file_path)
        
        self.input_max_len = input_max_len
        self.target_max_len = target_max_len
        self.tokenizer = tokenizer
        self.inputs = []
        self.targets = []

        #self._build()
        self._build2()
  
    def __len__(self):
        return len(self.inputs)
  
    def __getitem__(self, index):
        source_ids = self.inputs[index]["input_ids"].squeeze()
        target_ids = self.targets[index]["input_ids"].squeeze()

        source_mask = self.inputs[index]["attention_mask"].squeeze()
        target_mask = self.targets[index]["attention_mask"].squeeze()

        return {"source_ids": source_ids, "source_mask": source_mask, 
                "target_ids": target_ids, "target_mask": target_mask}

    def _make_record(self, title, body, genre_id):
        # ニュースタイトル生成タスク用の入出力形式に変換する。
        input = f"{body}"
        target = f"{title}"
        return input, target
  
    def _build(self):
        with open(self.file_path, "r", encoding="utf-8") as f:
            for line in f:
                line = line.strip().split("\t")
                assert len(line) == 3
                assert len(line[0]) > 0
                assert len(line[1]) > 0
                assert len(line[2]) > 0

                title = line[0]
                body = line[1]
                genre_id = line[2]

                input, target = self._make_record(title, body, genre_id)

                tokenized_inputs = self.tokenizer.batch_encode_plus(
                    [input], max_length=self.input_max_len, truncation=True, 
                    padding="max_length", return_tensors="pt"
                )

                tokenized_targets = self.tokenizer.batch_encode_plus(
                    [target], max_length=self.target_max_len, truncation=True, 
                    padding="max_length", return_tensors="pt"
                )

                self.inputs.append(tokenized_inputs)
                self.targets.append(tokenized_targets)

    def _make_record2(self, name, description, id):
        input = f"{description}"
        target = f"{name}"
        return input, target
  
    def _build2(self):
        with open(self.file_path, "r", encoding="utf-8") as f:
            for line in f:
                line = line.strip().split("\t")
                assert len(line) == 3
                assert len(line[0]) > 0
                assert len(line[1]) > 0
                assert len(line[2]) > 0

                id = line[0]
                name = line[1]
                description = line[2]

                input, target = self._make_record2(name, description, id)

                tokenized_inputs = self.tokenizer.batch_encode_plus(
                    [input], max_length=self.input_max_len, truncation=True, 
                    padding="max_length", return_tensors="pt"
                )

                tokenized_targets = self.tokenizer.batch_encode_plus(
                    [target], max_length=self.target_max_len, truncation=True, 
                    padding="max_length", return_tensors="pt"
                )

                self.inputs.append(tokenized_inputs)
                self.targets.append(tokenized_targets)

試しにテストデータ（test.tsv）を読み込み、トークナイズ結果をみてみます。

In [ ]:
# トークナイザー（SentencePiece）モデルの読み込み
tokenizer = T5Tokenizer.from_pretrained(MODEL_DIR, is_fast=True)

print(args_dict["data_dir"])
# テストデータセットの読み込み
train_dataset = TsvDataset(tokenizer, args_dict["data_dir"], "/content/train2.tsv", 
                           input_max_len=args_dict["max_input_length"], 
                           target_max_len=args_dict["max_target_length"])

Downloading:   0%|          | 0.00/804k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.79k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.92k [00:00<?, ?B/s]

/content
/content/train2.tsv


テストデータの1レコード目をみてみます。

In [ ]:
for data in train_dataset:
    print("A. 入力データの元になる文字列")
    print(tokenizer.decode(data["source_ids"]))
    print()
    print("B. 入力データ（Aの文字列がトークナイズされたトークンID列）")
    print(data["source_ids"])
    print()
    print("C. 出力データの元になる文字列")
    print(tokenizer.decode(data["target_ids"]))
    print()
    print("D. 出力データ（Cの文字列がトークナイズされたトークンID列）")
    print(data["target_ids"])
    break

A. 入力データの元になる文字列
【日本製生地使用、縫製までこだわりのプレミアムワイシャツ】生地は優れた技術力によって製造された播州織を使用。タイドアップとアンタイド、ジャケット合わせonとoff両方の着こなしにマッチするデザインです。【仕様・機能】■tiotio premium『抗菌』『消臭』『抗ウイルス』『静電気抑制』を付加した安全性の高い多機能加工。■japan fabric優れた技術力によって製造された日本製生地を使用■super easy iron形態安定性に優れ洗濯後のアイロン掛けも簡単です。【縫製仕様の特徴】播州織生地にクラシックな縫製仕様を施し、スタイリッシュに仕立てております。■播州織230年以上の歴史がある地場産業。糸から先に染めた豊かな色合いが特徴。■スプリットヨークフィット感を高めるためにヨークを背中の中心でバイアスに切替え、肩の動きにゆとりを与え快適な着心地に。■台<unk> 台<unk> のフロント部分を持ち上げた仕様を施し、台<unk> ボタンを外した時に<unk> が下がらずに美しく見えます■円錐形カフス曲線系で構成することで手首にフィット■ハギ仕様アームホールを曲線的に縫製することで立体的に仕上がり脇下のもたつきをなくします■<unk> 付け<unk> は厳選した天然貝を使用。台<unk> ・カフスの<unk> 付け部分を鳥足型にすることで、適度な浮きを持たせ着脱を容易にする仕様。【シルエット】《やや細め(スッキリ)》(当社比)■ゆとり感には個人差があります。サイズ表を確認の上、ご購入の目安としてご利用ください。【商品に関するご注意】■ブラウザやお使いのモニター環境、室内外等の撮影時の環境下での光加減により、実際の商品と掲載画像の色味が異なる場合がございます。■生地や仕様・デザインにより、着用感や実際のサイズ表に若干の誤差が生じる場合がございます。予めご了承ください。</s> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <pad> <

# 学習済みモデルの読み込み

In [ ]:
import torch
from torch.utils.data import Dataset, DataLoader
from transformers import T5ForConditionalGeneration, T5Tokenizer

# トークナイザー（SentencePiece）
tokenizer = T5Tokenizer.from_pretrained(MODEL_DIR, is_fast=True)

# 学習済みモデル
trained_model = T5ForConditionalGeneration.from_pretrained(MODEL_DIR)

# GPUの利用有無
USE_GPU = torch.cuda.is_available()
if USE_GPU:
    trained_model.cuda()

Downloading:   0%|          | 0.00/696 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/892M [00:00<?, ?B/s]

# 全テストデータの本文に対するタイトル生成

### **※必須実行ではない**

In [ ]:
import textwrap
from tqdm.auto import tqdm
from sklearn import metrics

# テストデータの読み込み
test_dataset = TsvDataset(tokenizer, args_dict["data_dir"], "/content/test2.tsv", 
                          input_max_len=args_dict["max_input_length"], 
                          target_max_len=args_dict["max_target_length"])

test_loader = DataLoader(test_dataset, batch_size=8, num_workers=4)

trained_model.eval()

inputs = []
outputs = []
targets = []

for batch in tqdm(test_loader):
    input_ids = batch['source_ids']
    input_mask = batch['source_mask']
    if USE_GPU:
        input_ids = input_ids.cuda()
        input_mask = input_mask.cuda()

    output = trained_model.generate(input_ids=input_ids, 
        attention_mask=input_mask, 
        max_length=args_dict["max_target_length"],
        temperature=1.0,          # 生成にランダム性を入れる温度パラメータ
        repetition_penalty=1.5,   # 同じ文の繰り返し（モード崩壊）へのペナルティ
        )

    output_text = [tokenizer.decode(ids, skip_special_tokens=True, 
                            clean_up_tokenization_spaces=False) 
                for ids in output]
    target_text = [tokenizer.decode(ids, skip_special_tokens=True, 
                               clean_up_tokenization_spaces=False) 
                for ids in batch["target_ids"]]
    input_text = [tokenizer.decode(ids, skip_special_tokens=True, 
                               clean_up_tokenization_spaces=False) 
                for ids in input_ids]

    inputs.extend(input_text)
    outputs.extend(output_text)
    targets.extend(target_text)

## 生成結果確認
形式
- generated: 生成されたタイトル
- actual: 人が作成したタイトル（正解）
- body: ニュース記事の本文

In [ ]:
for output, target, input in zip(outputs, targets, inputs):
    print("generated: " + output)
    print("actual:    " + target)
    print("body:      " + input)
    print()

## 任意の文章に対するタイトル生成テスト
**太字**
**テスト実行用：#generate_title()のコメントを外して適宜実行**

文章に合うタイトルを10個、自動生成してみます。

以下のコードではタイトルの多様性を生むために色々generateメソッドのパラメータを設定しています。パラメータの詳細は下記リンク先を参照してください。

- [generateメソッドのパラメータの意味](https://huggingface.co/transformers/main_classes/model.html#transformers.generation_utils.GenerationMixin.generate)

In [ ]:
# 文章の出典: https://qiita.com/sonoisa/items/cf0bc6c0ed4d244407b4
# 正解: LEGOで作るスマートロック　〜「Hey Siri 鍵開けて」を実現する方法 〜
body = """
これはLEGOとRaspberry Piで実用的なスマートロックを作り上げる物語です。
スマートロック・システムの全体構成は下図のようになります。図中右上にある塊が、全部LEGOで作られたスマートロックです。

特徴は、3Dプリンタ不要で、LEGOという比較的誰でも扱えるもので作られたハードウェアであるところ、見た目の野暮ったさと機能のスマートさを兼ね備え、エンジニア心をくすぐるポイント満載なところです。
なお、LEGO (レゴ)、LEGO Boost (ブースト) は LEGO Group (レゴグループ) の登録商標であり、この文書はレゴグループやその日本法人と一切関係はありません。

次のようなシチュエーションを経験したことはありませんか？

- 外出先にて、「そういや、鍵、閉めてきたかな？記憶がない…（ソワソワ）」
- 朝の通勤にて、駅に到着してみたら「あ、鍵閉め忘れた。戻るか…」
- 料理中に「あ、鍵閉め忘れた！でも、いま手が離せない。」
- 玄関先で「手は買い物で一杯。ポケットから鍵を出すのが大変。」
- 職場にて、夕方「そろそろ子供は家に帰ってきたかな？」
- 玄関にて「今日は傘いるかな？」

今回作るスマートロックは、次の機能でこれらを解決に導きます。

- 鍵の閉め忘れをSlackに通知してくれる。iPhoneで施錠状態を確認できる。
- 何処ででもiPhoneから施錠できる。
- 「Hey Siri 鍵閉めて（鍵開けて）」で施錠/開錠できる。
- 鍵の開閉イベントがiPhoneに通知され、帰宅が分かる。
- LEDの色で天気予報（傘の必要性）を教えてくれる（ただし、時間の都合で今回は説明省略）。

欲しくなりましたでしょうか？

以下、ムービー多めで機能の詳細と作り方について解説していきます。ハードウェアもソフトウェアもオープンソースとして公開します。
"""

In [ ]:
MAX_SOURCE_LENGTH = args_dict["max_input_length"]   # 入力される記事本文の最大トークン数
MAX_TARGET_LENGTH = args_dict["max_target_length"]  # 生成されるタイトルの最大トークン数

def preprocess_body(text):
    return normalize_text(text.replace("\n", " "))

def generate_title():
  # 推論モード設定
  trained_model.eval()

  # 前処理とトークナイズを行う
  inputs = [preprocess_body(body)]
  batch = tokenizer.batch_encode_plus(
      inputs, max_length=MAX_SOURCE_LENGTH, truncation=True, 
      padding="longest", return_tensors="pt")

  input_ids = batch['input_ids']
  input_mask = batch['attention_mask']
  if USE_GPU:
      input_ids = input_ids.cuda()
      input_mask = input_mask.cuda()

  # 生成処理を行う
  outputs = trained_model.generate(
      input_ids=input_ids, attention_mask=input_mask, 
      max_length=MAX_TARGET_LENGTH,
      temperature=1.0,          # 生成にランダム性を入れる温度パラメータ
      num_beams=10,             # ビームサーチの探索幅
      diversity_penalty=1.0,    # 生成結果の多様性を生み出すためのペナルティ
      num_beam_groups=10,       # ビームサーチのグループ数
      num_return_sequences=10,  # 生成する文の数
      repetition_penalty=1.5,   # 同じ文の繰り返し（モード崩壊）へのペナルティ
  )

  # 生成されたトークン列を文字列に変換する
  generated_titles = [tokenizer.decode(ids, skip_special_tokens=True, 
                                      clean_up_tokenization_spaces=False) 
                      for ids in outputs]

# 生成されたタイトルを表示する
for i, title in enumerate(generated_titles):
    print(f"{i+1:2}. {title}")

#generate_title()

# 文章に対するタイトル生成

文章に合うタイトルを10個、自動生成します。
以下のコードではタイトルの多様性を生むために色々generateメソッドのパラメータを設定しています。パラメータの詳細は下記リンク先を参照してください。

generateメソッドのパラメータの意味
要約をGenerateさせたい文章ファイルを読み込み<br>
ループ処理でファイルに生成された文章ｊを書き出していく<br>
<br>
形式：{ID}, {Name}, {要約文}, {説明文}

In [ ]:
%cd input/
%ls
%pwd

/content/drive/MyDrive/Colab Notebooks/data/input
t5_aoscs_20230113_t5_1001-2000.csv  t5_aoscs_20230113_t5_2001-3000.csv
t5_aoscs_20230113_t5_1-1000.csv     t5_aoscs_20230113_t5_3001-3672.csv


'/content/drive/MyDrive/Colab Notebooks/data/input'

In [ ]:
MAX_SOURCE_LENGTH = args_dict["max_input_length"]   # 入力される記事本文の最大トークン数
MAX_TARGET_LENGTH = args_dict["max_target_length"]  # 生成されるタイトルの最大トークン数

def preprocess_body(text):
    return normalize_text(text.replace("\n", " "))

#
def read_id_name_desc_line(line):
    #line = normalize_text(remove_brackets(line))
    row = line.split('|')
    id = row[0].split(",")[1]
    name = row[1]
    desc = row[2].replace('【商品詳細】', '')
    return id, name, desc

def inference_summary(input_file_path, output_file_path):

  # 推論モード設定
  trained_model.eval()

  with open(input_file_path) as f:
    inferenceis = []
    for index, line in enumerate(f):
      #Split（行, ID | Name | Descroptiom)
      id, name, desc = read_id_name_desc_line(line)
      #print(index)
      #print(id)
      #print(name)
      #print(desc)
      if index == 0:
        continue

      # 前処理とトークナイズを行う
      inputs = [preprocess_body(desc)]
      batch = tokenizer.batch_encode_plus(
          inputs, max_length=MAX_SOURCE_LENGTH, truncation=True, 
          padding="longest", return_tensors="pt")
      #print(inputs)
      #print(batch)

      input_ids = batch['input_ids']
      input_mask = batch['attention_mask']
      if USE_GPU:
          input_ids = input_ids.cuda()
          input_mask = input_mask.cuda()

      # 生成処理を行う
      outputs = trained_model.generate(
          input_ids=input_ids, attention_mask=input_mask, 
          max_length=MAX_TARGET_LENGTH,
          temperature=1.0,          # 生成にランダム性を入れる温度パラメータ
          num_beams=10,             # ビームサーチの探索幅
          diversity_penalty=1.0,    # 生成結果の多様性を生み出すためのペナルティ
          num_beam_groups=10,       # ビームサーチのグループ数
          num_return_sequences=10,  # 生成する文の数
          repetition_penalty=1.5,   # 同じ文の繰り返し（モード崩壊）へのペナルティ
      )
      #print(outputs)

      # 生成されたトークン列を文字列に変換する
      generated_titles = [tokenizer.decode(ids, skip_special_tokens=True, 
                                          clean_up_tokenization_spaces=False) 
                          for ids in outputs]

      """
      # 生成されたタイトルを表示する
      for i, title in enumerate(generated_titles):
          print(f"{i+1:2}. {title}")
      """

      #書き出す文字列をformat
      s = "{0},{1},{2},{3},{4}".format(index, id, name, generated_titles[0], desc)
      inferenceis.append(s)
      print(s)
      #if index == 3:
      #  break
      
  with open(output_file_path, mode='w') as f:
    for i, s in enumerate(inferenceis):
      #print(s)
      f.write(s+'\n')

## 要約を実行

*   入力ファイル名と出力先指定を
*   inference_summaryを実行(ファイルごとにループ上でCall)



In [ ]:

input_fld = fldGdriveColabMyDriveData + 'input/'
output_fld = fldGdriveColabMyDriveData + 'output/'

file_names = [
    "t5_aoscs_20230113_t5_1001-2000.csv", 
    "t5_aoscs_20230113_t5_2001-3000.csv", 
    "t5_aoscs_20230113_t5_3001-3672.csv"
  ]
#file_names = ["t5_aoscs_20230113_t5_1001-2000.csv"]

for f in file_names:
  input_file_path = input_fld + f
  output_file_path = output_fld + "inferenced_" + f
  inference_summary(input_file_path, output_file_path)

#input_file_path = "/content/drive/MyDrive/Colab Notebooks/data/input/t5_aoscs_20230113_t5_1-1000.csv"
#output_file_path = "/content/drive/MyDrive/Colab Notebooks/data/output/inferenced_t5_aoscs_20230113_t5_1-1000.csv"



1,67920,ボタンダウンスタンダードワイシャツ【キング&トール】,肌触りの良いイージーケアワイシャツ/洗濯後のお手入れも簡単,【肌触りの良いイージーケアワイシャツ】糸から企画し厳選された生地を使用した、程良いゆとりのスタンダードワイシャツです。肌触り抜群のコットン100%でスーパーイージーアイロン加工を施し、洗濯後のお手入れも簡単。ファッション性と機能性を兼ね備えたデザインは、スーツスタイルからジャケット・パンツスタイルまで幅広くコーディネート可能です。【仕様・機能】■SUPER EASY IRON…形態安定性に優れ洗濯後のアイロン掛けも簡単です。■OEKO-TEX(エコテックス)…繊維製品の国際的な安全基準であるエコテックス(R)に認証された生地から付属まですべてが厳しい基準をクリアした素材を使用、安全を安心して着用いただけます。【シルエット】《標準》　(当社比)　■ゆとり感には個人差があります。【サイズ詳細はこちら】からサイズ表を確認の上、ご購入の目安としてご利用ください。【商品に関するご注意】■平置き・メジャーでの採寸の為、素材や仕様等により実際の商品とサイズ表に若干の誤差が生じる場合がございます。■ブラウザやお使いのモニター環境、室内外等の撮影時の環境下での光加減により、実際の商品と掲載画像の色味が異なる場合がございます。予めご了承ください。,1001
2,67921,ボタンダウンスタンダードワイシャツ【キング&トール】,肌触りの良いイージーケアワイシャツ/洗濯後のお手入れも簡単,【肌触りの良いイージーケアワイシャツ】糸から企画し厳選された生地を使用した、程良いゆとりのスタンダードワイシャツです。肌触り抜群のコットン100%でスーパーイージーアイロン加工を施し、洗濯後のお手入れも簡単。ファッション性と機能性を兼ね備えたデザインは、スーツスタイルからジャケット・パンツスタイルまで幅広くコーディネート可能です。【仕様・機能】■SUPER EASY IRON…形態安定性に優れ洗濯後のアイロン掛けも簡単です。■OEKO-TEX(エコテックス)…繊維製品の国際的な安全基準であるエコテックス(R)に認証された生地から付属まですべてが厳しい基準をクリアした素材を使用、安全を安心して着用いただけます。【シルエット】《標準》　(当社比)　■ゆとり感には個人差があります。【